In [1]:
import datasets

def load_local_dataset(dsname):
    d = datasets.load_dataset('json', data_files=f'/workspace/data/{dsname}.json')
    d = d.cast_column('audio', datasets.features.Audio(sampling_rate=16000))
    return d

ovm = load_local_dataset('ovm')
vyst = load_local_dataset('vystadial2016')
pscr = load_local_dataset('pscr')

ovm['train'][0]

Using custom data configuration default-8f1be135afea2a5e


  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Dataset json downloaded and prepared to /workspace/.cache/huggingface/datasets/json/default-8f1be135afea2a5e/0.0.0/ac0ca5f5289a6cf108e706efcf040422dbbfa8e658dee6a819f20d76bb84d26b. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Dataset json downloaded and prepared to /workspace/.cache/huggingface/datasets/json/default-eec7a48f9eca7cd5/0.0.0/ac0ca5f5289a6cf108e706efcf040422dbbfa8e658dee6a819f20d76bb84d26b. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

{'audio': {'path': '/workspace/data/ovm/ovm_111218-621.wav',
  'array': array([ 0.00079346,  0.00073242,  0.00012207, ..., -0.00323486,
         -0.00177002, -0.00180054], dtype=float32),
  'sampling_rate': 16000},
 'sentence': 'co by novinář když václav havel byl v prezidentském úřadu a pak právě při psaní knížky prosím stručně vaše vzpomínka na václava havla'}

In [2]:
cv = datasets.load_dataset("mozilla-foundation/common_voice_8_0", "cs", split="train+validation", use_auth_token=True)
cv = cv.remove_columns(["accent", "age", "client_id", "down_votes", "gender", "locale", "segment", "up_votes"])
cv = cv.cast_column("audio", datasets.Audio(sampling_rate=16_000))
cv[0]

Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/cs/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)


{'path': 'cv-corpus-8.0-2022-01-19/cs/clips/common_voice_cs_20500740.mp3',
 'audio': {'path': 'cv-corpus-8.0-2022-01-19/cs/clips/common_voice_cs_20500740.mp3',
  'array': array([0.0000000e+00, 0.0000000e+00, 0.0000000e+00, ..., 6.3757376e-05,
         4.1789750e-05, 6.2637460e-05], dtype=float32),
  'sampling_rate': 16000},
 'sentence': 'To dělá to, že se tady chodí po lukách místo po cestičkách.'}

In [3]:
#all = datasets.interleave_datasets([ovm['train'], vyst['train'], pscr['train'], cv])
all = datasets.concatenate_datasets([ovm['train'], vyst['train'], pscr['train'], cv]).shuffle()
all[0]


{'audio': {'path': '/workspace/data/vystadial2016/train/10/62/vad-2015-09-20--12-34-27.561625.wav',
  'array': array([ 0.00564575,  0.00588989,  0.00363159, ..., -0.01358032,
         -0.01220703, -0.00946045], dtype=float32),
  'sampling_rate': 16000},
 'sentence': 'olomouc hlavní nádraží',
 'path': None}

In [4]:
common_voice_test = datasets.load_dataset("mozilla-foundation/common_voice_8_0", "cs", split="test", use_auth_token=True)
common_voice_test = common_voice_test.remove_columns(["accent", "age", "client_id", "down_votes", "gender", "locale", "segment", "up_votes"])
len(common_voice_test)

Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/cs/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8)


7267

In [5]:
import re
chars_to_remove_regex = '[\,\?\.\!\-\;\:\/\"\“\„\%\”\�\–\'\`\«\»\—\’\…]'


CHARS = {
    'ü': 'ue',
    'ö': 'oe',
    'ï': 'i',
    'ë': 'e',
    'ä': 'ae',
    'ã': 'a',
    'à': 'á',
    'ø': 'o',
    'è': 'é',
    'ê': 'é',
    'å': 'ó',
    'î': 'i',
    'ñ': 'ň',
    'ç': 's',
    'ľ': 'l',
    'ż': 'ž',
    'ł': 'w',
    'ć': 'č',
    'þ': 't',
    'ß': 'ss',
    'ę': 'en',
    'ą': 'an',
    'æ': 'ae',
  }

def replace_chars(sentence):
  result = ''
  for ch in sentence:
    new = CHARS[ch] if ch in CHARS else ch
    result += new

  return result


def remove_special_characters(batch):
    batch["sentence"] = re.sub(chars_to_remove_regex, ' ', batch["sentence"]).lower()
    batch["sentence"] = replace_chars(batch['sentence'])
    batch["sentence"] = " ".join([char for char in batch["sentence"].split(" ") if char != ""])
    return batch


In [6]:
all = all.map(remove_special_characters)
common_voice_test = common_voice_test.map(remove_special_characters)

0ex [00:00, ?ex/s]

Loading cached processed dataset at /workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/cs/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8/cache-900ef796264993e5.arrow


In [7]:
def extract_all_chars(batch):
  all_text = " ".join(batch["sentence"])
  vocab = list(set(all_text))
  return {"vocab": [vocab], "all_text": [all_text]}

In [8]:
vocab_train = all.map(extract_all_chars, batched=True, batch_size=-1, keep_in_memory=True, remove_columns=all.column_names)
vocab_list = list(set(vocab_train["vocab"][0]))
vocab_dict = {v: k for k, v in enumerate(sorted(vocab_list))}
vocab_dict

  0%|          | 0/1 [00:00<?, ?ba/s]

{' ': 0,
 'a': 1,
 'b': 2,
 'c': 3,
 'd': 4,
 'e': 5,
 'f': 6,
 'g': 7,
 'h': 8,
 'i': 9,
 'j': 10,
 'k': 11,
 'l': 12,
 'm': 13,
 'n': 14,
 'o': 15,
 'p': 16,
 'q': 17,
 'r': 18,
 's': 19,
 't': 20,
 'u': 21,
 'v': 22,
 'w': 23,
 'x': 24,
 'y': 25,
 'z': 26,
 'á': 27,
 'é': 28,
 'í': 29,
 'ó': 30,
 'ú': 31,
 'ý': 32,
 'č': 33,
 'ď': 34,
 'ě': 35,
 'ň': 36,
 'ř': 37,
 'š': 38,
 'ť': 39,
 'ů': 40,
 'ž': 41}

In [9]:
vocab_dict["|"] = vocab_dict[" "]
del vocab_dict[" "]
vocab_dict["[UNK]"] = len(vocab_dict)
vocab_dict["[PAD]"] = len(vocab_dict)
len(vocab_dict)

44

In [10]:
%cd ~/cs/cs2
%pwd

/workspace/cs/cs2


'/workspace/cs/cs2'

In [11]:
vocab_dict["[UNK]"] = len(vocab_dict)
vocab_dict["[PAD]"] = len(vocab_dict)
len(vocab_dict)

44

In [12]:
from transformers import Wav2Vec2CTCTokenizer

tokenizer = Wav2Vec2CTCTokenizer.from_pretrained("./", unk_token="[UNK]", pad_token="[PAD]", word_delimiter_token="|")

In [13]:
repo_name = "wav2vec2-xls-r-300m-cs-250"

In [14]:
from transformers import Wav2Vec2FeatureExtractor

feature_extractor = Wav2Vec2FeatureExtractor(feature_size=1, sampling_rate=16000, padding_value=0.0, do_normalize=True, return_attention_mask=True)

In [15]:
from transformers import Wav2Vec2Processor

processor = Wav2Vec2Processor(feature_extractor=feature_extractor, tokenizer=tokenizer)

In [16]:
# save tokenizer to folder
processor.save_pretrained(repo_name)

In [17]:
all[0]["path"]

In [18]:
all[0]["audio"]

{'path': '/workspace/data/vystadial2016/train/10/62/vad-2015-09-20--12-34-27.561625.wav',
 'array': array([ 0.00564575,  0.00588989,  0.00363159, ..., -0.01358032,
        -0.01220703, -0.00946045], dtype=float32),
 'sampling_rate': 16000}

In [19]:
from datasets import Audio
all = all.cast_column("audio", Audio(sampling_rate=16_000))
common_voice_test = common_voice_test.cast_column("audio", Audio(sampling_rate=16_000))

In [20]:
all[0]["audio"]

{'path': '/workspace/data/vystadial2016/train/10/62/vad-2015-09-20--12-34-27.561625.wav',
 'array': array([ 0.00564575,  0.00588989,  0.00363159, ..., -0.01358032,
        -0.01220703, -0.00946045], dtype=float32),
 'sampling_rate': 16000}

In [21]:
import IPython.display as ipd
import numpy as np
import random

rand_int = random.randint(0, len(all)-1)

print(all[rand_int]["sentence"])
ipd.Audio(data=all[rand_int]["audio"]["array"], autoplay=True, rate=16000)

dobrý den chtěl bych jet


In [22]:
def prepare_dataset(batch):
    audio = batch["audio"]

    # batched output is "un-batched"
    batch["input_values"] = processor(audio["array"], sampling_rate=audio["sampling_rate"]).input_values[0]
    batch["input_length"] = len(batch["input_values"])
    
    with processor.as_target_processor():
        batch["labels"] = processor(batch["sentence"]).input_ids
    return batch

In [23]:
all = all.map(prepare_dataset, remove_columns=all.column_names)
common_voice_test = common_voice_test.map(prepare_dataset, remove_columns=common_voice_test.column_names)

0ex [00:00, ?ex/s]

Loading cached processed dataset at /workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/cs/8.0.0/b8bc4d453193c06a43269b46cd87f075c70f152ac963b7f28f7a2760c45ec3e8/cache-fcc378c48562cf8c.arrow


In [24]:
import torch

from dataclasses import dataclass, field
from typing import Any, Dict, List, Optional, Union

@dataclass
class DataCollatorCTCWithPadding:
    """
    Data collator that will dynamically pad the inputs received.
    Args:
        processor (:class:`~transformers.Wav2Vec2Processor`)
            The processor used for proccessing the data.
        padding (:obj:`bool`, :obj:`str` or :class:`~transformers.tokenization_utils_base.PaddingStrategy`, `optional`, defaults to :obj:`True`):
            Select a strategy to pad the returned sequences (according to the model's padding side and padding index)
            among:
            * :obj:`True` or :obj:`'longest'`: Pad to the longest sequence in the batch (or no padding if only a single
              sequence if provided).
            * :obj:`'max_length'`: Pad to a maximum length specified with the argument :obj:`max_length` or to the
              maximum acceptable input length for the model if that argument is not provided.
            * :obj:`False` or :obj:`'do_not_pad'` (default): No padding (i.e., can output a batch with sequences of
              different lengths).
    """

    processor: Wav2Vec2Processor
    padding: Union[bool, str] = True

    def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
        # split inputs and labels since they have to be of different lenghts and need
        # different padding methods
        input_features = [{"input_values": feature["input_values"]} for feature in features]
        label_features = [{"input_ids": feature["labels"]} for feature in features]

        batch = self.processor.pad(
            input_features,
            padding=self.padding,
            return_tensors="pt",
        )
        with self.processor.as_target_processor():
            labels_batch = self.processor.pad(
                label_features,
                padding=self.padding,
                return_tensors="pt",
            )

        # replace padding with -100 to ignore loss correctly
        labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

        batch["labels"] = labels

        return batch

In [25]:
data_collator = DataCollatorCTCWithPadding(processor=processor, padding=True)

In [26]:
from datasets import load_metric

wer_metric = load_metric("wer")
cer_metric = load_metric("cer")
metrics = [wer_metric, cer_metric]

In [27]:
def compute_metrics(pred):
    pred_logits = pred.predictions
    pred_ids = np.argmax(pred_logits, axis=-1)

    pred.label_ids[pred.label_ids == -100] = processor.tokenizer.pad_token_id

    pred_str = processor.batch_decode(pred_ids)
    # we do not want to group tokens when computing the metrics
    label_str = processor.batch_decode(pred.label_ids, group_tokens=False)

    wer = wer_metric.compute(predictions=pred_str, references=label_str)
    cer = cer_metric.compute(predictions=pred_str, references=label_str)

    return {"wer": wer, "cer": cer}

In [28]:
from transformers import Wav2Vec2ForCTC

model = Wav2Vec2ForCTC.from_pretrained(
    #"comodoro/wav2vec2-xls-r-300m-cs-cv8", 
    "facebook/wav2vec2-xls-r-300m", 
    attention_dropout=0.1,
    hidden_dropout=0.2,
    feat_proj_dropout=0.0,
    mask_time_prob=0.1,
    layerdrop=0.1,
    ctc_loss_reduction="mean", 
    pad_token_id=processor.tokenizer.pad_token_id,
    vocab_size=len(processor.tokenizer),
)

Some weights of the model checkpoint at facebook/wav2vec2-xls-r-300m were not used when initializing Wav2Vec2ForCTC: ['project_hid.bias', 'project_q.weight', 'quantizer.weight_proj.bias', 'project_hid.weight', 'quantizer.weight_proj.weight', 'project_q.bias', 'quantizer.codevectors']
- This IS expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of Wav2Vec2ForCTC were not initialized from the model checkpoint at facebook/wav2vec2-xls-r-300m and are newly initialized: ['lm_head.weight', 'lm_head.bias']
You should probably TRAIN this model on a down-stream task to be able to use it 

In [29]:
model.freeze_feature_extractor()

/workspace/.local/lib/python3.8/site-packages/transformers/models/wav2vec2/modeling_wav2vec2.py:1700: FutureWarning: The method `freeze_feature_extractor` is deprecated and will be removed in Transformers v5.Please use the equivalent `freeze_feature_encoder` method instead.
  warnings.warn(


In [30]:
from transformers import TrainingArguments

training_args = TrainingArguments(
  output_dir=repo_name,
  group_by_length=True,
  per_device_train_batch_size=32,
  gradient_accumulation_steps=1,
  eval_accumulation_steps=1,
  evaluation_strategy="steps",
  num_train_epochs=5,
  gradient_checkpointing=True,
  fp16=True,
  save_steps=800,
  eval_steps=800,
  logging_steps=250,
  learning_rate=1e-4,
  warmup_steps=800,
  save_total_limit=2,
  report_to="tensorboard"
)

In [31]:
from transformers import Trainer

trainer = Trainer(
    model=model,
    data_collator=data_collator,
    args=training_args,
    compute_metrics=compute_metrics,
    train_dataset=all,
    eval_dataset=common_voice_test,
    tokenizer=processor.feature_extractor,
)

Using amp half precision backend


In [32]:
trainer.train()

The following columns in the training set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
/workspace/.local/lib/python3.8/site-packages/transformers/optimization.py:306: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use thePyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(
***** Running training *****
  Num examples = 159605
  Num Epochs = 5
  Instantaneous batch size per device = 32
  Total train batch size (w. parallel, distributed & accumulation) = 32
  Gradient Accumulation steps = 1
  Total optimization steps = 24940


The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 7267
  Batch size = 8
Saving model checkpoint to wav2vec2-xls-r-300m-cs-250/checkpoint-800
Configuration saved in wav2vec2-xls-r-300m-cs-250/checkpoint-800/config.json
Model weights saved in wav2vec2-xls-r-300m-cs-250/checkpoint-800/pytorch_model.bin
Configuration saved in wav2vec2-xls-r-300m-cs-250/checkpoint-800/preprocessor_config.json
Deleting older checkpoint [wav2vec2-xls-r-300m-cs-250/checkpoint-30400] due to args.save_total_limit
The following columns in the evaluation set  don't have a corresponding argument in `Wav2Vec2ForCTC.forward` and have been ignored: input_length.
***** Running Evaluation *****
  Num examples = 7267
  Batch size = 8
Saving model checkpoint to wav2vec2-xls-r-300m-cs-250/checkpoint-1600
Configuration saved in wav2vec2-xls-r-300m-cs-250/checkpoint-1600/config.json


TrainOutput(global_step=24940, training_loss=0.7262697845434511, metrics={'train_runtime': 53649.1292, 'train_samples_per_second': 14.875, 'train_steps_per_second': 0.465, 'total_flos': 1.1982083586402645e+20, 'train_loss': 0.7262697845434511, 'epoch': 5.0})

In [33]:
trainer.create_model_card()

Dropping the following result as it does not have all the necessary fields:
{}


In [34]:
model.save_pretrained('.')

Configuration saved in ./config.json
Model weights saved in ./pytorch_model.bin
